# Métodos iterativos para la álgebra lineal numérica

En los notebooks anteriores, vimos que podemos resolver EDPs lineales estacionarios al reducirlos, a través de una discretización en el espacio, a problemas de álgebra lineal, y vimos que hay **métodos directos** para resolverlos, como el método de eliminación Gaussiana (o factorización $LU$). Los métodos de esta índole se llaman "directos", ya que proveen un algoritmo que resuelve directamente el problema, con un algoritmo que garantizadamente termina después de un número de operaciones computacionales que se conoce de antemano.

**[1]** (Opcional.)

Para una matriz de tamaño $N \times N$, encuentra la *complejidad computacional* del algoritmo de eliminación Gaussiana, es decir, cómo escala el número total de operaciones requeridas con el tamaño $N$ del sistema.

### [1]

Claramente, si tenemos una matriz de $N \times N$ y queremos realizar eliminación gaussiana para evaular la matríz, debemos realizar para cada columna $j$ desde 1 hasta $N-1$, hay que realizar $N-j$ operaciones, es decir

\begin{equation}
\mathcal{O}(N)\approx \sum_{j=1}^{N-1} {N-j}=\sum_{j=1}^{N-1} {j} = \frac{(N-1)(N)}{2}
\end{equation}

Así, claramente este algoritmo tiene una complejidad cuadrática, es decir, que crece polinomialmente como un polinomio de grado 2, denotado por $\mathcal{O}(N^2)$

Sin embargo, también vimos que el método de eliminación Gaussiana resulta a menudo ser muy poco eficiente, ya que la matriz en cuestión tiene muchos ceros. Decimos que la matriz es **sparse** (inglés), o dispersa, rala, escasa, etc. en español. 

Existen otra clase muy distinta de algoritmos en la álgebra lineal numérica, los **métodos iterativos**. Si pensamos en los problemas estacionarios como literalmente el estado estacionario de una ecuación de evolución (artificial), es natural pensar en resolverlos con métodos iterativos, como ya hicimos en el caso 1D.

## El método de relajación 

El algoritmo iterativo más sencillo sirve para resolver ecuaciones lineales de tipo Poisson:

$$\nabla^2 V(\mathbf{x}) = -\rho(\mathbf{x}).$$

Vimos en el notebook anterior que al discretizar el operador $\nabla^2$ en 2D en una red cuadrada (con $h_x = h_y = h$), nos lleva a un sistema de ecuaciones (una para cada punto $(i,j)$ de la malla) de la forma

$$u_{i,j+1} + u_{i,j-1} + u_{i-1,j} + u_{i+1,j} - 4 u_{ij} = - h^2 \rho(x_{ij}).$$

Podemos convertir esta ecuación en método iterativo al despejar $u_{ij}$ e introducir un tiempo artificial:

$$u_{ij}^{(t+1)} = \textstyle \frac{1}{4} \left[ u_{i,j+1}^{(t)} + u_{i,j-1}^{(t)} + u_{i-1,j}^{(t)} + u_{i+1,j}^{(t)} + h^2 \rho(x_{ij}) \right]. \quad (*)$$

Eso se llama el **método de Jacobi**. Se llama un método de **relajación**, ya que la solución "se relaja" hacia el estado estacionario. Nótese que es necesario contar con dos matrices: una al paso $t$, y una al paso $t+1$.

**[2]** (i) Implementa el método de Jacobi y utilízalo para resolver los mismos problemas físicos que en el notebook 19. Nótese que la condición inicial es arbitraria, pero ¡las condiciones de frontera son cruciales!

(ii) ¿Está mejor este método o el de eliminación gaussiana para este problema? ¿Por qué?

(iii) ¿A cuál ecuación parcial diferencial de evolución corresponde la ecuación (*)?  De esta forma, ¿cómo podemos interpretar el método?

(iv) Calcula el estado estacionario (después de una evolución larga) y guárdala. Repite la evolución (desde la misma condición inicial) para calcular cómo cambia la distancia (en una norma adecuada) desde el estado estacionario en el tiempo, y grafícala. ¿Qué comportamiento tiene?

### [2] 

Este método es más eficiente que la elimiación gaussiana, dado que la complejidad de la elimnación gaussiana es cuadrática en la dimension de la malla deseada, mientras que este algoritmo tiene una complejidad dependiente del número de iteraciones pero que en principio es lineal respecto a ese número. Por otro lado, también permite que las evoluciones se estabilicen dando resultados relativamente más suaves.

La discretización de la euación de Poisson en dos dimensiones es muy similar a la ecuación de calor discretizada, donde la malla temporal y el coeficiente de difusion son tales que las constantes quedan de esa manera y donde el valor anterior de la función es la distribución de carga.

Así, podríamos interpretar que nuestra discretización de la ecuación de Poisson es un algoritmo que **difunde** la distribución de cargas (es decir, la carga eléctrica) por todo el espacio.

In [18]:
using Plots,Interact
gr()

Plots.GRBackend()

In [77]:
function jacobi(rho::Function,LX::Tuple{Float64,Float64},LY::Tuple{Float64,Float64},frontera=Tuple{Tuple{Float64,Float64},Tuple{Float64,Float64}};N=1000,h::Float64=1e-2,test=false)
    LX=LX[1]:h:LX[2]
    LY=LY[1]:h:LY[2]
    carga=[rho([LX[i],LY[j]]) for i in 1:length(LX),j in 1:length(LY)]
    carga=carga'
    U=rand(length(LY),length(LX))
    for t in 1:N
        IX=vcat(frontera[1][1]*ones(length(LX))',U[1:(end-1),:])
        FX=vcat(U[2:end,:],frontera[1][2]*ones(length(LX))')
        IY=hcat(frontera[2][1]*ones(length(LY)),U[:,1:(end-1)])
        FY=hcat(U[:,2:end],frontera[2][2]*ones(length(LY)))
        if test==true
            @show i
            @show IX
            @show FX
            @show IY
            @show FY
            @show U
        end
        U=1/4*(IX+FX+IY+FY+h^2*carga)
    end
    return (LX,LY,U)
end

jacobi (generic function with 2 methods)

, Tuple{Float64, Float64}, Tuple{Float64, Float64}) in module Main at In[53]:2 overwritten at In[77]:2.


In [78]:
function escalon(X;h=1e3,r=1e-1,p=2)
    if norm(X,p)<r
        return h
    else 
        return 0.0
    end
end

escalon (generic function with 1 method)

) in module Main at In[54]:2 overwritten at In[78]:2.


In [102]:
A=linspace(-1.0,1.0,100)
B=linspace(-1.0,1.0,100)
surface(A,B,[escalon([a,b],r=0.3) for a in A,b in B],aspect_ratio=:equal)

In [83]:
M=jacobi(A->escalon(A-[0.5,0.5],r=0.1,h=1e6)+escalon(A+[0.5,0.5],r=0.1,h=1e6)-escalon(A+[-0.5,0.5],r=0.1,h=1e6)-escalon(A-[-0.5,0.5],r=0.1,h=1e6),(-1.0,1.0),(-1.0,1.0),((0.0,0.0),(0.0,0.0)),N=3000)
display(surface(M[1],M[2],M[3]),title="potencial electrostático en dos dimensiones",xlabel="x",ylabel="y",zlabel="v(x,y)")
display(heatmap(M[1],M[2],M[3]).xlabel="x",ylabel="y")

In [81]:
M=jacobi(A->0.0,(-1.0,1.0),(-1.0,1.0),((0.0,0.0),(0.0,0.0)),N=3000)
display(surface(M[1],M[2],M[3],title="potencial electrostático en dos dimensiones",xlabel="x",ylabel="y",zlabel="v(x,y)"))
display(heatmap(M[1],M[2],M[3],xlabel="x",ylabel="y"))

(-1.0:0.01:1.0,-1.0:0.01:1.0,
[0.000210713 0.000423343 … 0.000420525 0.000209807; 0.000423344 0.00084229 … 0.000838672 0.00042052; … ; 0.000427938 0.000846972 … 0.000840836 0.000420122; 0.000211885 0.000427935 … 0.000420123 0.000210348])

In [86]:
M=jacobi(A->0.0,(-1.0,1.0),(-1.0,1.0),((1.0,0.0),(0.0,0.0)),N=3000)
display(surface(M[1],M[2],M[3],title="potencial electrostático en dos dimensiones",xlabel="x",ylabel="y",zlabel="v(x,y)"))
display(heatmap(M[1],M[2],M[3]),xlabel="x",ylabel="y")

In [97]:
function capacitor(X;d::Float64=0.5,l::Float64=1.0,v::Float64=1e5)
    if abs(X[1]-d/2)<0.01 && abs(X[2])<l/2
        return v
    elseif  abs(X[1]+d/2)<0.01 && abs(X[2])<l/2
        return -v
    else
        return 0.0
    end
end

capacitor (generic function with 1 method)

) in module Main at In[94]:2 overwritten at In[97]:2.


In [98]:
A=linspace(-1.0,1.0,100)
B=linspace(-1.0,1.0,100)
heatmap(A,B,[capacitor([a,b]) for a in A,b in B],aspect_ratio=:equal)

In [101]:
M=jacobi(A->capacitor(A),(-1.0,1.0),(-1.0,1.0),((0.0,0.0),(0.0,0.0)),N=10000)
display(surface(M[1],M[2],M[3],title="potencial electrostático en dos dimensiones",xlabel="x",ylabel="y",zlabel="v(x,y)"))
display(heatmap(M[1],M[2],M[3],xlabel="x",ylabel="y"))

El método de Jacobi converge lentamente, y no siempre converge. Otra forma de ver al método de Jacobi es el siguiente.

Descompongamos la matriz $\mathsf{M}$ que especifica el sistema 
de ecuaciones lineales de interés como 

$$ \mathsf{M} =  \mathsf{D} + \mathsf{R},$$ 

donde $\mathsf{D}$ es la parte diagonal y $\mathsf{R}$ el resto. 

El resolver $\mathsf{M} \cdot \mathbf{x} = \mathbf{b}$ es, entonces, equivalente a resolver

$$\mathsf{D} \cdot \mathbf{x} = \mathbf{b} - \mathsf{R} \cdot \mathbf{x}.$$

El punto es que ahora $\mathsf{D}$, siendo diagonal, es fácil de invertir, y llegamos al método iterativo

$$\mathbf{x}^{(t+1)} = \mathsf{D}^{-1} \cdot (\mathbf{b} - \mathsf{R} \cdot \mathbf{x}^{(t)}).$$

## El método de Gauss--Seidel 

Un algoritmo más eficiente que el de Jacobi es el método de **Gauss--Seidel**. La diferencia radica en que los nuevos valores calculados se *sobreescriben en cada paso en la misma matriz* (en lugar de almacenarse en una matriz diferente). 

**[3]** Implementa el método de Gauss--Seidel, y compara la distancia desde el estado estacionario con el método de Jacobi.

Existe otro método, llamado SOR ("Successive Over-Relaxation") que combina los dos métodos y puede ser (bastante) más eficiente. [¡Proyecto final!]